In [31]:
import pandas as pd
import matplotlib.pyplot as plt
import plotly.express as px
from ydata_profiling import ProfileReport
import os
import re
from dotenv import load_dotenv

# Import dataset

In [20]:
# Chargement API KEYS
load_dotenv()

API_KEY_S3 = os.environ["API_KEY_S3"]
API_SECRET_KEY_S3 = os.environ["API_SECRET_KEY_S3"]

bucket_name = "renergies99-bucket"
s3_prefix = "public"

In [21]:
df = pd.read_csv(
    "s3://renergies99-bucket/public/solar/raw_solar_data.csv",
    index_col=0,
    storage_options={
        "key": API_KEY_S3,
        "secret": API_SECRET_KEY_S3,
    }
)

In [22]:
df.shape

(2087, 15)

In [23]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 2087 entries, 2020-01-01 to 2025-09-30
Data columns (total 15 columns):
 #   Column                        Non-Null Count  Dtype  
---  ------                        --------------  -----  
 0   date                          2087 non-null   object 
 1   nb_event                      2087 non-null   int64  
 2   Proton Events                 913 non-null    object 
 3   Geomagnetic Activity Summary  2084 non-null   object 
 4   10cm                          2087 non-null   object 
 5   SSN                           2087 non-null   int64  
 6   Afr                           2087 non-null   object 
 7   Ap                            2084 non-null   object 
 8   Xray Bg                       2087 non-null   object 
 9   Proton Fluence (GT1MeV)       2087 non-null   object 
 10  Proton Fluence (GT10MeV)      2087 non-null   object 
 11  Electron Fluence (GT2MeV)     2087 non-null   object 
 12  K index Boulder               2087 non-null   float6

In [24]:
df.describe(include="all")

date     nb_event Proton Events  \
count         2087  2087.000000           913   
unique        2087          NaN           103   
top     2020-01-01          NaN         None.   
freq             1          NaN           810   
mean           NaN     4.291327           NaN   
std            NaN     5.260650           NaN   
min            NaN     1.000000           NaN   
25%            NaN     1.000000           NaN   
50%            NaN     2.000000           NaN   
75%            NaN     6.000000           NaN   
max            NaN    44.000000           NaN   

            Geomagnetic Activity Summary  10cm          SSN   Afr    Ap  \
count                               2084  2087  2087.000000  2087  2084   
unique                               393   201          NaN    60    68   
top     The geomagnetic field was quiet.   070          NaN   004   004   
freq                                 451    78          NaN   208   229   
mean                                 NaN   NaN    82.549114   NaN   NaN   
std                                  NaN   NaN    63.196830   NaN   NaN   
min                                  NaN   NaN     0.000000   NaN   NaN   
25%                                  NaN   NaN    24.000000   NaN   NaN   
50%                                  NaN   NaN    81.000000   NaN   NaN   
75%                                  NaN   NaN   130.000000   NaN   NaN   
max                                  NaN   NaN   382.000000   NaN   NaN   

       Xray Bg Proton Fluence (GT1MeV) Proton Fluence (GT10MeV)  \
count     2087                    2087                     2087   
unique     217                     310                      167   
top      <A1.0                 1.2e+05                  4.6e+04   
freq       202                      54                      201   
mean       NaN                     NaN                      NaN   
std        NaN                     NaN                      NaN   
min        NaN                     NaN                      NaN   
25%        NaN                     NaN                      NaN   
50%        NaN                     NaN                      NaN   
75%        NaN                     NaN                      NaN   
max        NaN                     NaN                      NaN   

       Electron Fluence (GT2MeV)  K index Boulder  K index Planetary Comments  
count                       2087      2087.000000        2087.000000      761  
unique                       248              NaN                NaN       69  
top                     1.30e+06              NaN                NaN    None.  
freq                          82              NaN                NaN      686  
mean                         NaN         1.986823           1.784379      NaN  
std                          NaN         0.911415           1.031990      NaN  
min                          NaN         0.000000           0.000000      NaN  
25%                          NaN         1.375000           1.000000      NaN  
50%                          NaN         2.000000           1.625000      NaN  
75%                          NaN         2.500000           2.375000      NaN  
max                          NaN         7.375000           8.625000      NaN

# EDA

In [25]:
# Nombre de  valeurs manquantes
valeurs_manquantes = df.isna().sum()
valeurs_manquantes

date                               0
nb_event                           0
Proton Events                   1174
Geomagnetic Activity Summary       3
10cm                               0
SSN                                0
Afr                                0
Ap                                 3
Xray Bg                            0
Proton Fluence (GT1MeV)            0
Proton Fluence (GT10MeV)           0
Electron Fluence (GT2MeV)          0
K index Boulder                    0
K index Planetary                  0
Comments                        1326
dtype: int64

In [26]:
# Pourcentage de valeurs manquantes
valeurs_manquantes_pourcent = (df.isna().sum() / df.shape[0]) * 100
valeurs_manquantes_pourcent

date                             0.000000
nb_event                         0.000000
Proton Events                   56.252995
Geomagnetic Activity Summary     0.143747
10cm                             0.000000
SSN                              0.000000
Afr                              0.000000
Ap                               0.143747
Xray Bg                          0.000000
Proton Fluence (GT1MeV)          0.000000
Proton Fluence (GT10MeV)         0.000000
Electron Fluence (GT2MeV)        0.000000
K index Boulder                  0.000000
K index Planetary                0.000000
Comments                        63.536176
dtype: float64

In [27]:
valeurs_manquantes_graph = valeurs_manquantes[valeurs_manquantes > 0].sort_values(ascending=False)

plt.figure(figsize=(10, 5))
# Prise en charge si valeurs manquetes à 0
if valeurs_manquantes_graph.empty:
    ax = plt.gca()
    ax.text(0.5, 0.5, "Aucune valeur manquante",
            ha="center", va="center", fontsize=12)
    ax.axis("off")
else:
    valeurs_manquantes_graph.plot(kind="bar")
    plt.title("Valeurs manquantes par colonne")
    plt.ylabel("Nombre de valeurs manquantes")
    plt.xticks(rotation=45, ha="right")

plt.show()

In [28]:
profile = ProfileReport(df, title="Analyse openwather", explorative=True)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 15/15 [00:00<00:00, 684.20it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Analyse temporelle

In [30]:
# Nettoyage date
df["date"] = pd.to_datetime(df["date"], errors="coerce")
df["nb_event"] = pd.to_numeric(df["nb_event"], errors="coerce")
df = df.sort_values("date")

# Visualisation Plotly
fig = px.line(
    df,
    x="date",
    y="nb_event",
    title="Évolution du nombre d'événements solaires dans le temps",
)

fig.show()

### analyse multivariée

In [32]:
def clean_numeric(col):
    return (col.astype(str)
            .str.replace(r"[^0-9\.\-]", "", regex=True)
            .replace("", None)
            .astype(float))

In [34]:
df.columns

Index(['date', 'nb_event', 'Proton Events', 'Geomagnetic Activity Summary',
       '10cm', 'SSN', 'Afr', 'Ap', 'Xray Bg', 'Proton Fluence (GT1MeV)',
       'Proton Fluence (GT10MeV)', 'Electron Fluence (GT2MeV)',
       'K index Boulder', 'K index Planetary', 'Comments'],
      dtype='object')

In [36]:
# Nettoyage
df["date"] = pd.to_datetime(df["date"], errors="coerce")
for col in ["nb_event", "SSN", "10cm", "Proton Fluence (GT1MeV)", "Electron Fluence (GT2MeV)"]:
    df[col] = clean_numeric(df[col])

df = df.sort_values("date")

# Plot multivarié
fig = px.line(
    df,
    x="date",
    y=["nb_event", "SSN", "10cm", "Proton Fluence (GT1MeV)"],
    title="Évolution croisée : activité solaire & flux de particules"
)

fig.update_layout(legend_title="Variables")
fig.show()

## Étude des indicateurs solaires